## Data extraction

In [1]:
import os
import zipfile

import pandas as pd
import geopandas as gpd

import re

## Extract files

In [6]:
import os

def get_zip_file(directory):
    zip_files = [file for file in os.listdir(directory) if file.endswith('.zip')]

    if len(zip_files) == 1:
        return os.path.join(directory, zip_files[0])
    elif len(zip_files) > 1:
        print("There is more than one .zip file in the directory.")
        # Handle the case when there are multiple .zip files
    else:
        print("No .zip file found in the directory.")
        # Handle the case when there are no .zip files

# Replace 'your_directory_path' with the path to your directory
#directory_path = '../'
#zip_file = get_zip_file(directory_path)

#if zip_file:
#    print(f"The .zip file found: {zip_file}")

The .zip file found: ../export_120155051.zip


In [11]:
directory_path = '../'
zip_file_path = get_zip_file(directory_path)
destination_path = '../data/'
starts_with = 'activities'

def extract_desired_files(zip_file_path, destination_path, starts_with):
    with zipfile.ZipFile(zip_file_path, 'r') as zip_ref:
        for file in zip_ref.namelist():
            if file.startswith(starts_with):
                zip_ref.extract(file, destination_path)

extract_desired_files(zip_file_path=zip_file_path,
                     destination_path=destination_path,
                     starts_with=starts_with)

print(f"Extraction complete. Files are in: {destination_path}")


Extraction complete. Files are in: ../data/


## Process .gpx files

In [3]:
def gpx_to_gdf(file_paths):
    """Creates a geodataframe from a list of .gpx files"""
    
    gdf_list = []

    for file_path in file_paths:
        if file_path.endswith(('.gpx')):
            file_name_clean = (re.sub(r"\.gpx$", "", file_path))
            #print(file_name_clean)
            try:
                gdf = gpd.read_file(file_path, layer='tracks')
                if gdf.shape[0]>0:
                    file_name_clean = re.sub(r"\.gpx$", "", file_path)
                    gdf['id_track'] = file_name_clean
                    gdf_list.append(gdf)
            except:
                print("Error", file)
    
    gdf_all = pd.concat(gdf_list, ignore_index=True)
    return gdf_all


gpx_directory = "../data/activities/"
gpx_files = [os.path.join(gpx_directory, file) for file in os.listdir(gpx_directory) if file.endswith('.gpx')]

gdf_all = gpx_to_gdf(gpx_files)
#gdf_all.plot()


ERROR 1: PROJ: proj_create_from_database: Open of /opt/conda/envs/gds/share/proj failed


In [5]:
from datetime import datetime
gdf_all.to_file(f"../data/strava_{datetime.today().strftime('%Y-%m-%d')}.gpkg", 
                driver='GPKG', 
                layer=f"bike_{datetime.today().strftime('%Y-%m-%d')}")

In [36]:
gdf_all.explore(tiles="CartoDB dark_matter",
               style_kwds={
                   "color":"yellow",
                   "opacity":0.2})

## Process .fit files (in progress)

In [64]:
!conda install conda-forge::python-fitparse -y

In [ ]:
!pip install fitdecode

In [4]:
import gzip
import shutil

In [32]:
with gzip.open('../data/raw/activities/10280340389.fit.gz', 'rb') as f_in:
    with open('../data/raw/activities/10280340389.fit', 'wb') as f_out:
        shutil.copyfileobj(f_in, f_out)

In [ ]:
import geopandas as gpd
from shapely.geometry import LineString
import fitdecode

fit = fitdecode.FitReader('../data/raw/activities/10280340389.fit')

timestamp_list = []
latitude_list = []
longitude_list = []

for frame in fit:
    if isinstance(frame, fitdecode.FitDataMessage) and frame.has_field('timestamp') \
            and frame.has_field('position_lat') and frame.has_field('position_long'):
    
        timestamp = frame.get_value('timestamp')
        latitude = frame.get_value('position_lat') * (180.0 / 2**31)  # Convert semicircles to degrees
        longitude = frame.get_value('position_long') * (180.0 / 2**31)  # Convert semicircles to degrees
    
        timestamp_list.append(timestamp)
        latitude_list.append(latitude)
        longitude_list.append(longitude)

geometry = [LineString(zip(longitude_list, latitude_list))]
gdf = gpd.GeoDataFrame(geometry=geometry, crs='EPSG:4326')
#gdf['timestamp'] = timestamp_list

In [65]:
gdf.explore(tiles="CartoDB positron")

In [54]:
fit_file = fitdecode.FitReader('../data/raw/activities/10280340389.fit')
for frame in fit_file:
    if isinstance(frame, fitdecode.records.FitDataMessage):
        print(f"data: {frame.name} #############")

        for field in frame.fields:
            # field is a FieldData object
            print(f"    {field.name}")
            if frame.has_field('position_lat') and frame.has_field('position_long'):
                print('latitude:', frame.get_value('position_lat')/ ((2**32)/360))
                print('longitude:', frame.get_value('position_long')/ ((2**32)/360))
    else:
        print("----- no data !!!!!!")

----- no data !!!!!!
----- no data !!!!!!
data: file_id #############
    time_created
    manufacturer
    type
    product
----- no data !!!!!!
data: activity #############
    local_timestamp
    timestamp
    total_timer_time
    num_sessions
----- no data !!!!!!
data: developer_data_id #############
    developer_data_index
    application_id
    application_version
----- no data !!!!!!
data: field_description #############
    fit_base_type_id
    developer_data_index
    field_definition_number
    field_name
----- no data !!!!!!
data: field_description #############
    fit_base_type_id
    developer_data_index
    field_definition_number
    field_name
----- no data !!!!!!
data: session #############
    sport
    start_time
    total_distance
    total_elapsed_time
    total_timer_time
    total_strides
    total_calories
    activity_type
    apple_health_uuid
----- no data !!!!!!
data: event #############
    event
    event_type
    timestamp
    timer_trigger
data: event 

In [36]:
import fitdecode

with fitdecode.FitReader('../data/raw/activities/10280340389.fit') as fit_file:
    for frame in fit_file:
        if frame.has_field('position_lat') and frame.has_field('position_long'):
            print('latitude:', frame.get_value('position_lat'))
            print('longitude:', frame.get_value('position_long'))

AttributeError: 'FitHeader' object has no attribute 'has_field'

In [ ]:
with fitdecode.FitReader('../data/raw/activities/10280340389.fit.gz') as fit_file:
    for frame in fit_file:
        if isinstance(frame, fitdecode.records.FitDataMessage):
            if frame.name == 'lap':
                # This frame contains data about a lap"
            elif frame.name == 'record':
                pass
                # This frame contains data about a "track point"

In [9]:
import astropy
import sys

In [19]:
fit_directory = "../data/raw/activities/"
fit_files = [os.path.join(fit_directory, file) for file in os.listdir(gpx_directory) if file.endswith('.fit.gz')]


for file_path in fit_files:

    counter = 0
    try:
        with fits.open('../data/raw/activities/10280340389.fit.gz') as hdul:
            data = hdul[1].data  # Assuming that the data is in the first extension
    
            # Create empty lists to store point geometries and timestamps
            points = []
            timestamps = []
        
            for row in data:
                # Assuming the FITS file has columns 'LATITUDE' and 'LONGITUDE'
                latitude = row['LATITUDE']
                longitude = row['LONGITUDE']
                
                # Add timestamp information (modify this based on the actual column name)
                timestamps.append(row['TIMESTAMP'])
        
                # Create a Point geometry
                point = Point(longitude, latitude)
                points.append(point)
    
    except OSError:
        counter += 1
        print("could not read file")

print(f"No se pudieron leer {counter} archivos de {len(fit_files)}")

could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file
could not read file


In [ ]:
gpx_directory = "../data/raw/activities/"
gpx_files = [os.path.join(gpx_directory, file) for file in os.listdir(gpx_directory) if file.endswith('.gpx')]

gdf_all = gpx_to_gdf(gpx_files)
#gdf_all.plot()

gdf_all.explore()

In [63]:
import fitparse

## Pendientes
- extraer los .fit.gz, sumar esas geodataframes a una lista para hacer concat de todo al final
- eliminar columnas que no se usan
- discernir entre "vuelta ciclista" y otros (caminata, etc.)
- joinear con "activities.csv"